In [1]:
import numpy as np
import pandas as pd
import scipy
from scipy.io import loadmat
import pickle
import seaborn as sns
sns.set()
import matplotlib.pyplot as plt
from sklearn.model_selection import train_test_split
from scipy.stats import norm
import h5py
import os
import csv

In [2]:
def pointer_to_data(array_of_pointers, bbDict):
    idps = []

    for i in range(0, array_of_pointers.shape[1]):
        point = array_of_pointers[:, i][0]
        dset = bbDict[point]
        data = dset[:]

        list = [chr(c[0]) for c in data]
        new = ""
        for x in list:
            new += x
        idps.append(new)
    return idps

In [3]:
biobank_file = '../../../../workspace12eBETA_Andrei.mat'
mat = h5py.File(biobank_file, 'r')

subject_IDs_unique = np.transpose(mat['subject_IDs_unique'], (1,0)).flatten().astype(int)
# IDPs1 = np.transpose(mat['IDPs1'], (1,0))
vars_i = np.transpose(mat['vars_i'], (1,0))
vars_i_deconf = np.transpose(mat['vars_i_deconf'], (1,0))
IDPs1_i_deconf = np.transpose(mat['IDPs1_i_deconf'], (1,0))

FileNotFoundError: [Errno 2] Unable to open file (unable to open file: name = '../../../../workspace12eBETA_Andrei.mat', errno = 2, error message = 'No such file or directory', flags = 0, o_flags = 0)

In [4]:
for key in list(mat.keys())[1:]:
    print(key, mat[key].shape)

I (1, 1)
IDP_categories (1, 3921)
IDP_category_names (16, 1)
IDP_names (1, 3921)
IDP_reordering (1, 3921)
IDPs (3921, 46743)
IDPs1 (3921, 42897)
IDPs1_i (3921, 42897)
IDPs1_i_deconf (3921, 42897)
IDPs1_i_deconfnoage (3921, 42897)
IDPs2 (3921, 42897)
IDPs2_i (3921, 42897)
IDPs2_i_deconf (3921, 42897)
IDPs2_i_deconfnoage (3921, 42897)
IDPs_i (3921, 46743)
IDPs_i_deconf (3921, 46743)
IDPs_i_deconfnoage (3921, 46743)
QC_IDP_names (1, 16)
QC_IDPs (16, 46743)
QC_IDPs1 (16, 42897)
QC_IDPs2 (16, 42897)
WSNAME (7, 1)
age (1, 46743)
age0 (1, 42897)
age1 (1, 42897)
age2 (1, 42897)
ans (1, 26)
birth_date (1, 42897)
conf (613, 46743)
conf1 (613, 42897)
conf12 (613, 42897)
conf2 (613, 42897)
conf_FST2 (1, 46743)
conf_NEWEDDY (1, 46743)
conf_SCALING_SWI (1, 46743)
conf_SCALING_T1 (1, 46743)
conf_SCALING_T2 (1, 46743)
conf_SCALING_dMRI (1, 46743)
conf_SCALING_rfMRI (1, 46743)
conf_SCALING_tfMRI (1, 46743)
conf_TE_rfMRI (1, 46743)
conf_TE_tfMRI (1, 46743)
conf_TablePos_COG_Table (1, 46743)
conf_TablePo

In [5]:
IDP_names = mat['IDP_names']
IDP_names = np.array(pointer_to_data(IDP_names, mat)).reshape(1, -1)

counter = 0
for item in IDP_names[0]:
    if str(item).startswith('IDP'):
        counter+=1

print('IDP_names: {} | IDP_names starting with IDP: {}'.format(len(IDP_names[0]), counter))

for idx, item in enumerate(IDP_names[0]):
    print('{:4} - {:}'.format(idx, item))
    
# np.savetxt('IDP_names.txt', IDP_names, fmt='%s')
if os.path.exists('IDP_names.txt'):
    os.remove('IDP_names.txt')
with open('IDP_names.txt', 'w', newline='') as file:
    for item in IDP_names[0]:
        file.write(item + '\n')

IDP_names: 3921 | IDP_names starting with IDP: 872
   0 - IDP_T1_SIENAX_peripheral_grey_normalised_volume
   1 - IDP_T1_SIENAX_peripheral_grey_unnormalised_volume
   2 - IDP_T1_SIENAX_CSF_normalised_volume
   3 - IDP_T1_SIENAX_CSF_unnormalised_volume
   4 - IDP_T1_SIENAX_grey_normalised_volume
   5 - IDP_T1_SIENAX_grey_unnormalised_volume
   6 - IDP_T1_SIENAX_white_normalised_volume
   7 - IDP_T1_SIENAX_white_unnormalised_volume
   8 - IDP_T1_SIENAX_brain-normalised_volume
   9 - IDP_T1_SIENAX_brain-unnormalised_volume
  10 - IDP_T1_FIRST_left_thalamus_volume
  11 - IDP_T1_FIRST_right_thalamus_volume
  12 - IDP_T1_FIRST_left_caudate_volume
  13 - IDP_T1_FIRST_right_caudate_volume
  14 - IDP_T1_FIRST_left_putamen_volume
  15 - IDP_T1_FIRST_right_putamen_volume
  16 - IDP_T1_FIRST_left_pallidum_volume
  17 - IDP_T1_FIRST_right_pallidum_volume
  18 - IDP_T1_FIRST_left_hippocampus_volume
  19 - IDP_T1_FIRST_right_hippocampus_volume
  20 - IDP_T1_FIRST_left_amygdala_volume
  21 - IDP_T1_FIR

In [6]:
IDP_categories = np.transpose(mat['IDP_categories'], (1,0)).flatten()

IDP_category_names = ['Regional and Tissue Volume',
                      'Cortical Area',
                      'Cortical Thickness',
                      'Regional and Tissue Intensity',
                      'Cortical Grey-White Contrast',
                      'White Matter Hyperintensity Colume',
                      'Regional T2*',
                      'WM Tract FA',
                      'WM Tract MO',
                      'WM Tract Diffusivity',
                      'WM Tract ICVF',
                      'WM Tract OD',
                      'WM Tract ISOVF',
                      'tfMRI Activation',
                      'rfMRI Node Amplitude',
                      'rfMRI Connectivity']

IDP_categories_new = []
for idx, elem in enumerate(IDP_categories):
    IDP_categories_new.append(IDP_category_names[int(elem)-1])
    
if os.path.exists('IDP_categories.txt'):
    os.remove('IDP_categories.txt')
with open('IDP_categories.txt', 'w', newline='') as file:
    for item in IDP_categories_new:
        file.write(item + '\n')

In [7]:
list(set(IDP_categories_new))

['Regional and Tissue Intensity',
 'WM Tract OD',
 'Cortical Thickness',
 'WM Tract ISOVF',
 'Cortical Grey-White Contrast',
 'Cortical Area',
 'Regional and Tissue Volume',
 'WM Tract Diffusivity',
 'rfMRI Connectivity',
 'WM Tract ICVF',
 'rfMRI Node Amplitude',
 'White Matter Hyperintensity Colume',
 'WM Tract MO',
 'WM Tract FA',
 'Regional T2*',
 'tfMRI Activation']

In [8]:
# qNum=np.concatenate((np.arange(0,18),np.arange(889,894)))
# tmp=np.ones(IDP_names.shape ,dtype=bool)
# tmp[:,qNum]=False
# IDP_names=IDP_names[tmp]

In [9]:
varsHeader = mat['varsHeader']
varsHeader = np.array(varsHeader)
varsHeader = pointer_to_data(np.transpose(varsHeader), mat)
varsHeader = np.transpose(varsHeader)

for idx, item in enumerate(varsHeader):
    print('{:5} - {:}'.format(idx, item))
    
# np.savetxt('varsHeader.txt', np.expand_dims(varsHeader, axis=0), fmt='%s')
if os.path.exists('varsHeader.txt'):
    os.remove('varsHeader.txt')
with open('varsHeader.txt', 'w', newline='') as file:
    for item in varsHeader:
        file.write(item + '\n')

    0 - Ethnic background (0.0)
    1 - Ethnic background (1.0)
    2 - Ethnic background (2.0)
    3 - Genotype measurement batch (0.0)
    4 - Heterozygosity (0.0)
    5 - Heterozygosity, PCA corrected (0.0)
    6 - Missingness (0.0)
    7 - Genetic principal components (0.1)
    8 - Genetic principal components (0.2)
    9 - Genetic principal components (0.3)
   10 - Genetic principal components (0.4)
   11 - Genetic principal components (0.5)
   12 - Genetic principal components (0.6)
   13 - Genetic principal components (0.7)
   14 - Genetic principal components (0.8)
   15 - Genetic principal components (0.9)
   16 - Genetic principal components (0.10)
   17 - Genetic principal components (0.11)
   18 - Genetic principal components (0.12)
   19 - Genetic principal components (0.13)
   20 - Genetic principal components (0.14)
   21 - Genetic principal components (0.15)
   22 - Genetic principal components (0.16)
   23 - Genetic principal components (0.17)
   24 - Genetic principal

In [10]:
varsHeader = np.loadtxt("varsHeader.txt", dtype=str, delimiter='\n')
for idx, item in enumerate(varsHeader):
    print('{:5} - {:}'.format(idx, item))

TypeError: control character 'delimiter' cannot be a newline (`\r` or `\n`).

In [ ]:
with open('varsHeader.txt') as f:
    varsHeader = f.readlines()
    varsHeader = [l.strip('\n\r') for l in varsHeader]
    
for idx, item in enumerate(varsHeader):
    print('{:5} - {:}'.format(idx, item))

    0 - Ethnic background (0.0)
    1 - Ethnic background (1.0)
    2 - Ethnic background (2.0)
    3 - Genotype measurement batch (0.0)
    4 - Heterozygosity (0.0)
    5 - Heterozygosity, PCA corrected (0.0)
    6 - Missingness (0.0)
    7 - Genetic principal components (0.1)
    8 - Genetic principal components (0.2)
    9 - Genetic principal components (0.3)
   10 - Genetic principal components (0.4)
   11 - Genetic principal components (0.5)
   12 - Genetic principal components (0.6)
   13 - Genetic principal components (0.7)
   14 - Genetic principal components (0.8)
   15 - Genetic principal components (0.9)
   16 - Genetic principal components (0.10)
   17 - Genetic principal components (0.11)
   18 - Genetic principal components (0.12)
   19 - Genetic principal components (0.13)
   20 - Genetic principal components (0.14)
   21 - Genetic principal components (0.15)
   22 - Genetic principal components (0.16)
   23 - Genetic principal components (0.17)
   24 - Genetic principal

In [12]:
varsHeader

['Ethnic background (0.0)',
 'Ethnic background (1.0)',
 'Ethnic background (2.0)',
 'Genotype measurement batch (0.0)',
 'Heterozygosity (0.0)',
 'Heterozygosity, PCA corrected (0.0)',
 'Missingness (0.0)',
 'Genetic principal components (0.1)',
 'Genetic principal components (0.2)',
 'Genetic principal components (0.3)',
 'Genetic principal components (0.4)',
 'Genetic principal components (0.5)',
 'Genetic principal components (0.6)',
 'Genetic principal components (0.7)',
 'Genetic principal components (0.8)',
 'Genetic principal components (0.9)',
 'Genetic principal components (0.10)',
 'Genetic principal components (0.11)',
 'Genetic principal components (0.12)',
 'Genetic principal components (0.13)',
 'Genetic principal components (0.14)',
 'Genetic principal components (0.15)',
 'Genetic principal components (0.16)',
 'Genetic principal components (0.17)',
 'Genetic principal components (0.18)',
 'Genetic principal components (0.19)',
 'Genetic principal components (0.20)',
 

In [13]:
varsVARS = mat['varsVARS']
varsVARS = np.array(varsVARS)
varsVARS = pointer_to_data(np.transpose(varsVARS), mat)
varsVARS = np.transpose(varsVARS)

for idx, item in enumerate(varsVARS):
    print('{:5} - {:}'.format(idx, item))
    
# np.savetxt('varsHeader.txt', np.expand_dims(varsHeader, axis=0), fmt='%s')
if os.path.exists('varsVARS.txt'):
    os.remove('varsVARS.txt')
with open('varsVARS.txt', 'w', newline='') as file:
    for item in varsVARS:
        file.write(item + '\n')

    0 - 21000-0.0
    1 - 21000-1.0
    2 - 21000-2.0
    3 - 22000-0.0
    4 - 22003-0.0
    5 - 22004-0.0
    6 - 22005-0.0
    7 - 22009-0.1
    8 - 22009-0.2
    9 - 22009-0.3
   10 - 22009-0.4
   11 - 22009-0.5
   12 - 22009-0.6
   13 - 22009-0.7
   14 - 22009-0.8
   15 - 22009-0.9
   16 - 22009-0.10
   17 - 22009-0.11
   18 - 22009-0.12
   19 - 22009-0.13
   20 - 22009-0.14
   21 - 22009-0.15
   22 - 22009-0.16
   23 - 22009-0.17
   24 - 22009-0.18
   25 - 22009-0.19
   26 - 22009-0.20
   27 - 22009-0.21
   28 - 22009-0.22
   29 - 22009-0.23
   30 - 22009-0.24
   31 - 22009-0.25
   32 - 22009-0.26
   33 - 22009-0.27
   34 - 22009-0.28
   35 - 22009-0.29
   36 - 22009-0.30
   37 - 22009-0.31
   38 - 22009-0.32
   39 - 22009-0.33
   40 - 22009-0.34
   41 - 22009-0.35
   42 - 22009-0.36
   43 - 22009-0.37
   44 - 22009-0.38
   45 - 22009-0.39
   46 - 22009-0.40
   47 - 22011-0.0
   48 - 22011-0.1
   49 - 22012-0.0
   50 - 22012-0.1
   51 - 22013-0.0
   52 - 22013-0.1
   53 - 22018-0

In [14]:
varsVARS = np.loadtxt("varsVARS.txt", dtype=str, delimiter='\n')
for idx, item in enumerate(varsVARS):
    print('{:5} - {:}'.format(idx, item))

TypeError: control character 'delimiter' cannot be a newline (`\r` or `\n`).

In [16]:
with open('varsVARS.txt') as f:
    varsVARS = f.readlines()
    varsVARS = [l.strip('\n\r') for l in varsVARS]
    
for idx, item in enumerate(varsVARS):
    print('{:5} - {:}'.format(idx, item))

    0 - 21000-0.0
    1 - 21000-1.0
    2 - 21000-2.0
    3 - 22000-0.0
    4 - 22003-0.0
    5 - 22004-0.0
    6 - 22005-0.0
    7 - 22009-0.1
    8 - 22009-0.2
    9 - 22009-0.3
   10 - 22009-0.4
   11 - 22009-0.5
   12 - 22009-0.6
   13 - 22009-0.7
   14 - 22009-0.8
   15 - 22009-0.9
   16 - 22009-0.10
   17 - 22009-0.11
   18 - 22009-0.12
   19 - 22009-0.13
   20 - 22009-0.14
   21 - 22009-0.15
   22 - 22009-0.16
   23 - 22009-0.17
   24 - 22009-0.18
   25 - 22009-0.19
   26 - 22009-0.20
   27 - 22009-0.21
   28 - 22009-0.22
   29 - 22009-0.23
   30 - 22009-0.24
   31 - 22009-0.25
   32 - 22009-0.26
   33 - 22009-0.27
   34 - 22009-0.28
   35 - 22009-0.29
   36 - 22009-0.30
   37 - 22009-0.31
   38 - 22009-0.32
   39 - 22009-0.33
   40 - 22009-0.34
   41 - 22009-0.35
   42 - 22009-0.36
   43 - 22009-0.37
   44 - 22009-0.38
   45 - 22009-0.39
   46 - 22009-0.40
   47 - 22011-0.0
   48 - 22011-0.1
   49 - 22012-0.0
   50 - 22012-0.1
   51 - 22013-0.0
   52 - 22013-0.1
   53 - 22018-0

In [35]:
vars_categories = np.zeros(np.array(varsHeader).shape)
vars_categories[0:3] = 1 # Ethnic Background
vars_categories[3:60] = 2 # Genetic Markers
vars_categories[60:69] = 3 # Physical Activity
vars_categories[69:75] = 2
vars_categories[75:107] = 4 # Early Life Factors
vars_categories[107:123] = 5 # Data Collection Duration
vars_categories[123:650] = 6 # Lifestyle
vars_categories[650:706] = 3
vars_categories[706:782] = 6
vars_categories[782:790] = 3
vars_categories[790:814] = 6
vars_categories[814:833] = 3
vars_categories[833:1074] = 6
vars_categories[1074:1089] = 3
vars_categories[1089:2778] = 7 # Diet
vars_categories[2778:2916] = 8 # Alcohol 
vars_categories[2916:3038] = 9 # Tobacco
vars_categories[3038:3298] = 10 # Physical Measurements
vars_categories[3298:3478] = 11 # Skeletal Measurements
vars_categories[3478:4292] = 12 # Cardiac & Circulartory Measurements
vars_categories[4292:5047] = 13 # Hearing Test
vars_categories[5047] = 12
vars_categories[5048:5482] = 14 # Eye Test
vars_categories[5482:5815] = 15 # Physical Test
vars_categories[5815:6283] = 16 # Blood Assays
vars_categories[6283:7450] = 17 # Cognitive Tests
vars_categories[7450:17230] = 18 # Medical History
vars_categories[17230:] = 19 # Mental Health

vars_category_names = ['Ethnic Background',
                      'Genetic Markers',
                      'Physical Activity',
                      'Early Life Factors',
                      'Data Collection Duration',
                      'Lifestyle',
                      'Diet',
                      'Alcohol',
                      'Tobacco',
                      'Physical Measurements',
                      'Skeletal Measurements',
                      'Cardiac & Circulartory Measurements',
                      'Hearing Test',
                      'Eye Test',
                      'Physical Test',
                      'Blood Assays',
                      'Cognitive Tests',
                      'Medical History',
                      'Mental Health',
                     ]

vars_categories_new = []
for idx, elem in enumerate(vars_categories):
    vars_categories_new.append(vars_category_names[int(elem)-1])

    
if os.path.exists('vars_categories.txt'):
    os.remove('vars_categories.txt')
with open('vars_categories.txt', 'w', newline='') as file:
    for item in vars_categories_new:
        file.write(item + '\n')

In [36]:
vars_categories.shape

(17527,)

# 1. Male & Female Test Datasets for IDPs and nIDPs

In [37]:
male_test = np.loadtxt('male_test.txt').astype(int)
female_test = np.loadtxt('female_test.txt').astype(int)

male_validation = np.loadtxt('male_validation.txt').astype(int)
female_validation = np.loadtxt('female_validation.txt').astype(int)

female_testA = np.loadtxt('female_testA.txt').astype(int)
female_testB = np.loadtxt('female_testB.txt').astype(int)

male_testA = np.loadtxt('male_testA.txt').astype(int)
male_testB = np.loadtxt('male_testB.txt').astype(int)

In [38]:
counter = 0
for subject in subject_IDs_unique:
    subject = int('2' + str(subject))
    if subject in male_test:
        counter += 1
        
print(len(male_test), counter)

4364 4364


In [39]:
counter = 0
for subject in male_test:
    subj = subject - 20000000
    if subj not in subject_IDs_unique:
        print('Exlude the following subject:', subject)

In [40]:
counter = 0
for subject in subject_IDs_unique:
    subject = int('2' + str(subject))
    if subject in female_test:
        counter += 1
        
print(len(female_test), counter)

5020 5020


In [41]:
counter = 0
for subject in female_test:
    subj = subject - 20000000
    if subj not in subject_IDs_unique:
        print('Exlude the following subject:', subject)

In [42]:
counter = 0
for subject in subject_IDs_unique:
    subject = int('2' + str(subject))
    if subject in male_validation:
        counter += 1
        
print(len(male_validation), counter)

1091 1091


In [43]:
counter = 0
for subject in subject_IDs_unique:
    subject = int('2' + str(subject))
    if subject in female_validation:
        counter += 1
        
print(len(female_validation), counter)

1255 1255


In [44]:
counter = 0
for subject in subject_IDs_unique:
    subject = int('2' + str(subject))
    if subject in male_testA:
        counter += 1
        
print(len(male_testA), counter)

2182 2182


In [45]:
counter = 0
for subject in female_testA:
    subj = subject - 20000000
    if subj not in subject_IDs_unique:
        print('Exlude the following subject:', subject)

In [46]:
counter = 0
for subject in subject_IDs_unique:
    subject = int('2' + str(subject))
    if subject in female_testB:
        counter += 1
        
print(len(female_testB), counter)

2510 2510


In [ ]:
# subjects_male = []
# # IDPs1_male = []
# vars_i_deconf_male = []
# IDPs1_i_deconf_male = []

# vars_i_male = []

# for subject in male_test:
#     subj = subject - 20000000
#     if subj in subject_IDs_unique:
#         idx = np.where(subject_IDs_unique == subj)
#         subjects_male.append(subject)
# #         IDPs1_male.append(IDPs1[idx].flatten())
#         vars_i_deconf_male.append(vars_i_deconf[idx].flatten())
#         IDPs1_i_deconf_male.append(IDPs1_i_deconf[idx].flatten())
        
#         vars_i_male.append(vars_i[idx].flatten())
        
# subjects_male = np.array(subjects_male)
# # IDPs1_male = np.array(IDPs1_male)
# vars_i_deconf_male = np.array(vars_i_deconf_male)
# IDPs1_i_deconf_male = np.array(IDPs1_i_deconf_male)

# vars_i_male = np.array(vars_i_male)

# if os.path.exists('male_test_IDPs.h5'):
#     os.remove('male_test_IDPs.h5')
# h5f = h5py.File('male_test_IDPs.h5', 'w')
# h5f.create_dataset('subjects', data=subjects_male)
# # h5f.create_dataset('IDPs1', data=IDPs1_male)
# h5f.create_dataset('vars_i_deconf', data=vars_i_deconf_male)
# h5f.create_dataset('IDPs1_i_deconf', data=IDPs1_i_deconf_male)

# h5f.create_dataset('vars_i', data=vars_i_male)

# h5f.close()

In [48]:
subjects_male = []
# IDPs1_male = []
vars_i_deconf_male = []
IDPs1_i_deconf_male = []

for subject in male_test:
    subj = subject - 20000000
    if subj in subject_IDs_unique:
        idx = np.where(subject_IDs_unique == subj)
        subjects_male.append(subject)
#         IDPs1_male.append(IDPs1[idx].flatten())
        vars_i_deconf_male.append(vars_i_deconf[idx].flatten())
        IDPs1_i_deconf_male.append(IDPs1_i_deconf[idx].flatten())
        
subjects_male = np.array(subjects_male)
# IDPs1_male = np.array(IDPs1_male)
vars_i_deconf_male = np.array(vars_i_deconf_male)
IDPs1_i_deconf_male = np.array(IDPs1_i_deconf_male)

if os.path.exists('male_test_IDPs.h5'):
    os.remove('male_test_IDPs.h5')
h5f = h5py.File('male_test_IDPs.h5', 'w')
h5f.create_dataset('subjects', data=subjects_male)
# h5f.create_dataset('IDPs1', data=IDPs1_male)
h5f.create_dataset('vars_i_deconf', data=vars_i_deconf_male)
h5f.create_dataset('IDPs1_i_deconf', data=IDPs1_i_deconf_male)
h5f.close()

In [ ]:
# subjects_female = []
# # IDPs1_female = []
# vars_i_deconf_female = []
# IDPs1_i_deconf_female = []

# vars_i_female = []

# for subject in female_testA:
#     subj = subject - 20000000
#     if subj in subject_IDs_unique:
#         idx = np.where(subject_IDs_unique == subj)
#         subjects_female.append(subject)
# #         IDPs1_female.append(IDPs1[idx].flatten())
#         vars_i_deconf_female.append(vars_i_deconf[idx].flatten())
#         IDPs1_i_deconf_female.append(IDPs1_i_deconf[idx].flatten())
        
#         vars_i_female.append(vars_i[idx].flatten())
        
# subjects_female = np.array(subjects_female)
# # IDPs1_female = np.array(IDPs1_female)
# vars_i_deconf_female = np.array(vars_i_deconf_female)
# IDPs1_i_deconf_female = np.array(IDPs1_i_deconf_female)

# vars_i_female = np.array(vars_i_female)

# if os.path.exists('female_testA_IDPs.h5'):
#     os.remove('female_testA_IDPs.h5')
# h5f = h5py.File('female_testA_IDPs.h5', 'w')
# h5f.create_dataset('subjects', data=subjects_female)
# # h5f.create_dataset('IDPs1', data=IDPs1_female)
# h5f.create_dataset('vars_i_deconf', data=vars_i_deconf_female)
# h5f.create_dataset('IDPs1_i_deconf', data=IDPs1_i_deconf_female)

# h5f.create_dataset('vars_i', data=vars_i_female)

# h5f.close()

In [26]:
subjects_female = []
# IDPs1_female = []
vars_i_deconf_female = []
IDPs1_i_deconf_female = []

for subject in female_testA:
    subj = subject - 20000000
    if subj in subject_IDs_unique:
        idx = np.where(subject_IDs_unique == subj)
        subjects_female.append(subject)
#         IDPs1_female.append(IDPs1[idx].flatten())
        vars_i_deconf_female.append(vars_i_deconf[idx].flatten())
        IDPs1_i_deconf_female.append(IDPs1_i_deconf[idx].flatten())
        
subjects_female = np.array(subjects_female)
# IDPs1_female = np.array(IDPs1_female)
vars_i_deconf_female = np.array(vars_i_deconf_female)
IDPs1_i_deconf_female = np.array(IDPs1_i_deconf_female)

if os.path.exists('female_testA_IDPs.h5'):
    os.remove('female_testA_IDPs.h5')
h5f = h5py.File('female_testA_IDPs.h5', 'w')
h5f.create_dataset('subjects', data=subjects_female)
# h5f.create_dataset('IDPs1', data=IDPs1_female)
h5f.create_dataset('vars_i_deconf', data=vars_i_deconf_female)
h5f.create_dataset('IDPs1_i_deconf', data=IDPs1_i_deconf_female)
h5f.close()

In [ ]:
# subjects_male = []
# # IDPs1_male = []
# vars_i_deconf_male = []
# IDPs1_i_deconf_male = []

# vars_i_male = []

# for subject in male_testA:
#     subj = subject - 20000000
#     if subj in subject_IDs_unique:
#         idx = np.where(subject_IDs_unique == subj)
#         subjects_male.append(subject)
# #         IDPs1_male.append(IDPs1[idx].flatten())
#         vars_i_deconf_male.append(vars_i_deconf[idx].flatten())
#         IDPs1_i_deconf_male.append(IDPs1_i_deconf[idx].flatten())
        
#         vars_i_male.append(vars_i[idx].flatten())
        
# subjects_male = np.array(subjects_male)
# # IDPs1_male = np.array(IDPs1_male)
# vars_i_deconf_male = np.array(vars_i_deconf_male)
# IDPs1_i_deconf_male = np.array(IDPs1_i_deconf_male)

# vars_i_male = np.array(vars_i_male)

# if os.path.exists('male_testA_IDPs.h5'):
#     os.remove('male_testA_IDPs.h5')
# h5f = h5py.File('male_testA_IDPs.h5', 'w')
# h5f.create_dataset('subjects', data=subjects_male)
# # h5f.create_dataset('IDPs1', data=IDPs1_male)
# h5f.create_dataset('vars_i_deconf', data=vars_i_deconf_male)
# h5f.create_dataset('IDPs1_i_deconf', data=IDPs1_i_deconf_male)

# h5f.create_dataset('vars_i', data=vars_i_male)

# h5f.close()

In [27]:
subjects_male = []
# IDPs1_male = []
vars_i_deconf_male = []
IDPs1_i_deconf_male = []

for subject in male_testA:
    subj = subject - 20000000
    if subj in subject_IDs_unique:
        idx = np.where(subject_IDs_unique == subj)
        subjects_male.append(subject)
#         IDPs1_male.append(IDPs1[idx].flatten())
        vars_i_deconf_male.append(vars_i_deconf[idx].flatten())
        IDPs1_i_deconf_male.append(IDPs1_i_deconf[idx].flatten())
        
subjects_male = np.array(subjects_male)
# IDPs1_male = np.array(IDPs1_male)
vars_i_deconf_male = np.array(vars_i_deconf_male)
IDPs1_i_deconf_male = np.array(IDPs1_i_deconf_male)

if os.path.exists('male_testA_IDPs.h5'):
    os.remove('male_testA_IDPs.h5')
h5f = h5py.File('male_testA_IDPs.h5', 'w')
h5f.create_dataset('subjects', data=subjects_male)
# h5f.create_dataset('IDPs1', data=IDPs1_male)
h5f.create_dataset('vars_i_deconf', data=vars_i_deconf_male)
h5f.create_dataset('IDPs1_i_deconf', data=IDPs1_i_deconf_male)
h5f.close()

In [49]:
subjects_female = []
# IDPs1_female = []
vars_i_deconf_female = []
IDPs1_i_deconf_female = []

vars_i_female = []

for subject in female_testB:
    subj = subject - 20000000
    if subj in subject_IDs_unique:
        idx = np.where(subject_IDs_unique == subj)
        subjects_female.append(subject)
#         IDPs1_female.append(IDPs1[idx].flatten())
        vars_i_deconf_female.append(vars_i_deconf[idx].flatten())
        IDPs1_i_deconf_female.append(IDPs1_i_deconf[idx].flatten())
        
        vars_i_female.append(vars_i[idx].flatten())
        
subjects_female = np.array(subjects_female)
# IDPs1_female = np.array(IDPs1_female)
vars_i_deconf_female = np.array(vars_i_deconf_female)
IDPs1_i_deconf_female = np.array(IDPs1_i_deconf_female)

vars_i_female = np.array(vars_i_female)

if os.path.exists('female_testB_IDPs.h5'):
    os.remove('female_testB_IDPs.h5')
h5f = h5py.File('female_testB_IDPs.h5', 'w')
h5f.create_dataset('subjects', data=subjects_female)
# h5f.create_dataset('IDPs1', data=IDPs1_female)
h5f.create_dataset('vars_i_deconf', data=vars_i_deconf_female)
h5f.create_dataset('IDPs1_i_deconf', data=IDPs1_i_deconf_female)

h5f.create_dataset('vars_i', data=vars_i_female)

h5f.close()

In [28]:
# subjects_female = []
# # IDPs1_female = []
# vars_i_deconf_female = []
# IDPs1_i_deconf_female = []

# for subject in female_testB:
#     subj = subject - 20000000
#     if subj in subject_IDs_unique:
#         idx = np.where(subject_IDs_unique == subj)
#         subjects_female.append(subject)
# #         IDPs1_female.append(IDPs1[idx].flatten())
#         vars_i_deconf_female.append(vars_i_deconf[idx].flatten())
#         IDPs1_i_deconf_female.append(IDPs1_i_deconf[idx].flatten())
        
# subjects_female = np.array(subjects_female)
# # IDPs1_female = np.array(IDPs1_female)
# vars_i_deconf_female = np.array(vars_i_deconf_female)
# IDPs1_i_deconf_female = np.array(IDPs1_i_deconf_female)

# if os.path.exists('female_testB_IDPs.h5'):
#     os.remove('female_testB_IDPs.h5')
# h5f = h5py.File('female_testB_IDPs.h5', 'w')
# h5f.create_dataset('subjects', data=subjects_female)
# # h5f.create_dataset('IDPs1', data=IDPs1_female)
# h5f.create_dataset('vars_i_deconf', data=vars_i_deconf_female)
# h5f.create_dataset('IDPs1_i_deconf', data=IDPs1_i_deconf_female)
# h5f.close()

In [ ]:
# subjects_male = []
# # IDPs1_male = []
# vars_i_deconf_male = []
# IDPs1_i_deconf_male = []

# vars_i_male = []

# for subject in male_testB:
#     subj = subject - 20000000
#     if subj in subject_IDs_unique:
#         idx = np.where(subject_IDs_unique == subj)
#         subjects_male.append(subject)
# #         IDPs1_male.append(IDPs1[idx].flatten())
#         vars_i_deconf_male.append(vars_i_deconf[idx].flatten())
#         IDPs1_i_deconf_male.append(IDPs1_i_deconf[idx].flatten())
        
#         vars_i_male.append(vars_i[idx].flatten())
        
# subjects_male = np.array(subjects_male)
# # IDPs1_male = np.array(IDPs1_male)
# vars_i_deconf_male = np.array(vars_i_deconf_male)
# IDPs1_i_deconf_male = np.array(IDPs1_i_deconf_male)

# vars_i_male = np.array(vars_i_male)

# if os.path.exists('male_testB_IDPs.h5'):
#     os.remove('male_testB_IDPs.h5')
# h5f = h5py.File('male_testB_IDPs.h5', 'w')
# h5f.create_dataset('subjects', data=subjects_male)
# # h5f.create_dataset('IDPs1', data=IDPs1_male)
# h5f.create_dataset('vars_i_deconf', data=vars_i_deconf_male)
# h5f.create_dataset('IDPs1_i_deconf', data=IDPs1_i_deconf_male)

# h5f.create_dataset('vars_i', data=vars_i_male)

# h5f.close()

In [29]:
subjects_male = []
# IDPs1_male = []
vars_i_deconf_male = []
IDPs1_i_deconf_male = []

for subject in male_testB:
    subj = subject - 20000000
    if subj in subject_IDs_unique:
        idx = np.where(subject_IDs_unique == subj)
        subjects_male.append(subject)
#         IDPs1_male.append(IDPs1[idx].flatten())
        vars_i_deconf_male.append(vars_i_deconf[idx].flatten())
        IDPs1_i_deconf_male.append(IDPs1_i_deconf[idx].flatten())
        
subjects_male = np.array(subjects_male)
# IDPs1_male = np.array(IDPs1_male)
vars_i_deconf_male = np.array(vars_i_deconf_male)
IDPs1_i_deconf_male = np.array(IDPs1_i_deconf_male)

if os.path.exists('male_testB_IDPs.h5'):
    os.remove('male_testB_IDPs.h5')
h5f = h5py.File('male_testB_IDPs.h5', 'w')
h5f.create_dataset('subjects', data=subjects_male)
# h5f.create_dataset('IDPs1', data=IDPs1_male)
h5f.create_dataset('vars_i_deconf', data=vars_i_deconf_male)
h5f.create_dataset('IDPs1_i_deconf', data=IDPs1_i_deconf_male)
h5f.close()

In [ ]:
# subjects_male = []
# # IDPs1_male = []
# vars_i_deconf_male = []
# IDPs1_i_deconf_male = []

# vars_i_male = []

# for subject in male_validation:
#     subj = subject - 20000000
#     if subj in subject_IDs_unique:
#         idx = np.where(subject_IDs_unique == subj)
#         subjects_male.append(subject)
# #         IDPs1_male.append(IDPs1[idx].flatten())
#         vars_i_deconf_male.append(vars_i_deconf[idx].flatten())
#         IDPs1_i_deconf_male.append(IDPs1_i_deconf[idx].flatten())
        
#         vars_i_male.append(vars_i[idx].flatten())
        
# subjects_male = np.array(subjects_male)
# # IDPs1_male = np.array(IDPs1_male)
# vars_i_deconf_male = np.array(vars_i_deconf_male)
# IDPs1_i_deconf_male = np.array(IDPs1_i_deconf_male)

# vars_i_male = np.array(vars_i_male)

# if os.path.exists('male_validation_IDPs.h5'):
#     os.remove('male_validation_IDPs.h5')
# h5f = h5py.File('male_validation_IDPs.h5', 'w')
# h5f.create_dataset('subjects', data=subjects_male)
# # h5f.create_dataset('IDPs1', data=IDPs1_male)
# h5f.create_dataset('vars_i_deconf', data=vars_i_deconf_male)
# h5f.create_dataset('IDPs1_i_deconf', data=IDPs1_i_deconf_male)

# h5f.create_dataset('vars_i', data=vars_i_male)

# h5f.close()

In [30]:
subjects_male = []
# IDPs1_male = []
vars_i_deconf_male = []
IDPs1_i_deconf_male = []

for subject in male_validation:
    subj = subject - 20000000
    if subj in subject_IDs_unique:
        idx = np.where(subject_IDs_unique == subj)
        subjects_male.append(subject)
#         IDPs1_male.append(IDPs1[idx].flatten())
        vars_i_deconf_male.append(vars_i_deconf[idx].flatten())
        IDPs1_i_deconf_male.append(IDPs1_i_deconf[idx].flatten())
        
subjects_male = np.array(subjects_male)
# IDPs1_male = np.array(IDPs1_male)
vars_i_deconf_male = np.array(vars_i_deconf_male)
IDPs1_i_deconf_male = np.array(IDPs1_i_deconf_male)

if os.path.exists('male_validation_IDPs.h5'):
    os.remove('male_validation_IDPs.h5')
h5f = h5py.File('male_validation_IDPs.h5', 'w')
h5f.create_dataset('subjects', data=subjects_male)
# h5f.create_dataset('IDPs1', data=IDPs1_male)
h5f.create_dataset('vars_i_deconf', data=vars_i_deconf_male)
h5f.create_dataset('IDPs1_i_deconf', data=IDPs1_i_deconf_male)
h5f.close()

In [ ]:
# subjects_female = []
# # IDPs1_female = []
# vars_i_deconf_female = []
# IDPs1_i_deconf_female = []

# vars_i_female = []

# for subject in female_test:
#     subj = subject - 20000000
#     if subj in subject_IDs_unique:
#         idx = np.where(subject_IDs_unique == subj)
#         subjects_female.append(subject)
# #         IDPs1_female.append(IDPs1[idx].flatten())
#         vars_i_deconf_female.append(vars_i_deconf[idx].flatten())
#         IDPs1_i_deconf_female.append(IDPs1_i_deconf[idx].flatten())
        
#         vars_i_female.append(vars_i[idx].flatten())
        
# subjects_female = np.array(subjects_female)
# # IDPs1_female = np.array(IDPs1_female)
# vars_i_deconf_female = np.array(vars_i_deconf_female)
# IDPs1_i_deconf_female = np.array(IDPs1_i_deconf_female)

# vars_i_female = np.array(vars_i_female)

# if os.path.exists('female_test_IDPs.h5'):
#     os.remove('female_test_IDPs.h5')
# h5f = h5py.File('female_test_IDPs.h5', 'w')
# h5f.create_dataset('subjects', data=subjects_female)
# # h5f.create_dataset('IDPs1', data=IDPs1_female)
# h5f.create_dataset('vars_i_deconf', data=vars_i_deconf_female)
# h5f.create_dataset('IDPs1_i_deconf', data=IDPs1_i_deconf_female)

# h5f.create_dataset('vars_i', data=vars_i_female)

# h5f.close()

In [31]:
subjects_female = []
# IDPs1_female = []
vars_i_deconf_female = []
IDPs1_i_deconf_female = []

for subject in female_test:
    subj = subject - 20000000
    if subj in subject_IDs_unique:
        idx = np.where(subject_IDs_unique == subj)
        subjects_female.append(subject)
#         IDPs1_female.append(IDPs1[idx].flatten())
        vars_i_deconf_female.append(vars_i_deconf[idx].flatten())
        IDPs1_i_deconf_female.append(IDPs1_i_deconf[idx].flatten())
        
subjects_female = np.array(subjects_female)
# IDPs1_female = np.array(IDPs1_female)
vars_i_deconf_female = np.array(vars_i_deconf_female)
IDPs1_i_deconf_female = np.array(IDPs1_i_deconf_female)

if os.path.exists('female_test_IDPs.h5'):
    os.remove('female_test_IDPs.h5')
h5f = h5py.File('female_test_IDPs.h5', 'w')
h5f.create_dataset('subjects', data=subjects_female)
# h5f.create_dataset('IDPs1', data=IDPs1_female)
h5f.create_dataset('vars_i_deconf', data=vars_i_deconf_female)
h5f.create_dataset('IDPs1_i_deconf', data=IDPs1_i_deconf_female)
h5f.close()

In [ ]:
# subjects_female = []
# # IDPs1_female = []
# vars_i_deconf_female = []
# IDPs1_i_deconf_female = []

# vars_i_female = []

# for subject in female_validation:
#     subj = subject - 20000000
#     if subj in subject_IDs_unique:
#         idx = np.where(subject_IDs_unique == subj)
#         subjects_female.append(subject)
# #         IDPs1_female.append(IDPs1[idx].flatten())
#         vars_i_deconf_female.append(vars_i_deconf[idx].flatten())
#         IDPs1_i_deconf_female.append(IDPs1_i_deconf[idx].flatten())
        
#         vars_i_female.append(vars_i[idx].flatten())
        
# subjects_female = np.array(subjects_female)
# # IDPs1_female = np.array(IDPs1_female)
# vars_i_deconf_female = np.array(vars_i_deconf_female)
# IDPs1_i_deconf_female = np.array(IDPs1_i_deconf_female)

# vars_i_female = np.array(vars_i_female)

# if os.path.exists('female_validation_IDPs.h5'):
#     os.remove('female_validation_IDPs.h5')
# h5f = h5py.File('female_validation_IDPs.h5', 'w')
# h5f.create_dataset('subjects', data=subjects_female)
# # h5f.create_dataset('IDPs1', data=IDPs1_female)
# h5f.create_dataset('vars_i_deconf', data=vars_i_deconf_female)
# h5f.create_dataset('IDPs1_i_deconf', data=IDPs1_i_deconf_female)

# h5f.create_dataset('vars_i', data=vars_i_female)

# h5f.close()

In [32]:
subjects_female = []
# IDPs1_female = []
vars_i_deconf_female = []
IDPs1_i_deconf_female = []

for subject in female_validation:
    subj = subject - 20000000
    if subj in subject_IDs_unique:
        idx = np.where(subject_IDs_unique == subj)
        subjects_female.append(subject)
#         IDPs1_female.append(IDPs1[idx].flatten())
        vars_i_deconf_female.append(vars_i_deconf[idx].flatten())
        IDPs1_i_deconf_female.append(IDPs1_i_deconf[idx].flatten())
        
subjects_female = np.array(subjects_female)
# IDPs1_female = np.array(IDPs1_female)
vars_i_deconf_female = np.array(vars_i_deconf_female)
IDPs1_i_deconf_female = np.array(IDPs1_i_deconf_female)

if os.path.exists('female_validation_IDPs.h5'):
    os.remove('female_validation_IDPs.h5')
h5f = h5py.File('female_validation_IDPs.h5', 'w')
h5f.create_dataset('subjects', data=subjects_female)
# h5f.create_dataset('IDPs1', data=IDPs1_female)
h5f.create_dataset('vars_i_deconf', data=vars_i_deconf_female)
h5f.create_dataset('IDPs1_i_deconf', data=IDPs1_i_deconf_female)
h5f.close()

In [33]:
# print(IDPs1_female.shape)|
print(vars_i_deconf_female.shape)
print(IDPs1_i_deconf_female.shape)

(1255, 17527)
(1255, 3921)


In [34]:
# print(IDPs1_female.shape)|
print(vars_i_deconf_male.shape)
print(IDPs1_i_deconf_male.shape)

(1091, 17527)
(1091, 3921)


In [35]:
# test = h5py.File('../../Analysis/male_test_IDPs.h5', 'r')
test = h5py.File('male_validation_IDPs.h5', 'r')
test.keys()

<KeysViewHDF5 ['IDPs1_i_deconf', 'subjects', 'vars_i_deconf']>

In [36]:
test = h5py.File('male_validation_IDPs.h5', 'r')
test.keys()
for key in list(test.keys()):
    print(key, test[key].shape)

IDPs1_i_deconf (1091, 3921)
subjects (1091,)
vars_i_deconf (1091, 17527)


# 2. Male & Female Test Datasets for IDPs nodeconfage

In [50]:
biobank_file = '../../../../workspace12eBETA.mat'
mat = h5py.File(biobank_file, 'r')

subject_IDs_unique = np.transpose(mat['subject_IDs_unique'], (1,0)).flatten().astype(int)
IDPs1_i_deconfnoage = np.transpose(mat['IDPs1_i_deconfnoage'], (1,0))

In [51]:
IDP_names = mat['IDP_names']
IDP_names = np.array(pointer_to_data(IDP_names, mat)).reshape(1, -1)

counter = 0
for item in IDP_names[0]:
    if str(item).startswith('IDP'):
        counter+=1

print('IDP_names: {} | IDP_names starting with IDP: {}'.format(len(IDP_names[0]), counter))

for idx, item in enumerate(IDP_names[0]):
    print('{:4} - {:}'.format(idx, item))
    
if os.path.exists('IDP_names.txt'):
    os.remove('IDP_names.txt')
with open('IDP_names.txt', 'w', newline='') as file:
    for item in IDP_names[0]:
        file.write(item + '\n')

IDP_names: 3921 | IDP_names starting with IDP: 872
   0 - IDP_T1_SIENAX_peripheral_grey_normalised_volume
   1 - IDP_T1_SIENAX_peripheral_grey_unnormalised_volume
   2 - IDP_T1_SIENAX_CSF_normalised_volume
   3 - IDP_T1_SIENAX_CSF_unnormalised_volume
   4 - IDP_T1_SIENAX_grey_normalised_volume
   5 - IDP_T1_SIENAX_grey_unnormalised_volume
   6 - IDP_T1_SIENAX_white_normalised_volume
   7 - IDP_T1_SIENAX_white_unnormalised_volume
   8 - IDP_T1_SIENAX_brain-normalised_volume
   9 - IDP_T1_SIENAX_brain-unnormalised_volume
  10 - IDP_T1_FIRST_left_thalamus_volume
  11 - IDP_T1_FIRST_right_thalamus_volume
  12 - IDP_T1_FIRST_left_caudate_volume
  13 - IDP_T1_FIRST_right_caudate_volume
  14 - IDP_T1_FIRST_left_putamen_volume
  15 - IDP_T1_FIRST_right_putamen_volume
  16 - IDP_T1_FIRST_left_pallidum_volume
  17 - IDP_T1_FIRST_right_pallidum_volume
  18 - IDP_T1_FIRST_left_hippocampus_volume
  19 - IDP_T1_FIRST_right_hippocampus_volume
  20 - IDP_T1_FIRST_left_amygdala_volume
  21 - IDP_T1_FIR

1759 - IDP_dMRI_TBSS_L3_Superior_cerebellar_peduncle_R
1760 - IDP_dMRI_TBSS_L3_Superior_cerebellar_peduncle_L
1761 - IDP_dMRI_TBSS_L3_Cerebral_peduncle_R
1762 - IDP_dMRI_TBSS_L3_Cerebral_peduncle_L
1763 - IDP_dMRI_TBSS_L3_Anterior_limb_of_internal_capsule_R
1764 - IDP_dMRI_TBSS_L3_Anterior_limb_of_internal_capsule_L
1765 - IDP_dMRI_TBSS_L3_Posterior_limb_of_internal_capsule_R
1766 - IDP_dMRI_TBSS_L3_Posterior_limb_of_internal_capsule_L
1767 - IDP_dMRI_TBSS_L3_Retrolenticular_part_of_internal_capsule_R
1768 - IDP_dMRI_TBSS_L3_Retrolenticular_part_of_internal_capsule_L
1769 - IDP_dMRI_TBSS_L3_Anterior_corona_radiata_R
1770 - IDP_dMRI_TBSS_L3_Anterior_corona_radiata_L
1771 - IDP_dMRI_TBSS_L3_Superior_corona_radiata_R
1772 - IDP_dMRI_TBSS_L3_Superior_corona_radiata_L
1773 - IDP_dMRI_TBSS_L3_Posterior_corona_radiata_R
1774 - IDP_dMRI_TBSS_L3_Posterior_corona_radiata_L
1775 - IDP_dMRI_TBSS_L3_Posterior_thalamic_radiation_R
1776 - IDP_dMRI_TBSS_L3_Posterior_thalamic_radiation_L
1777 - IDP_dMR

3258 - rfMRI connectivity (ICA100 edge 829)
3259 - rfMRI connectivity (ICA100 edge 830)
3260 - rfMRI connectivity (ICA100 edge 831)
3261 - rfMRI connectivity (ICA100 edge 832)
3262 - rfMRI connectivity (ICA100 edge 833)
3263 - rfMRI connectivity (ICA100 edge 834)
3264 - rfMRI connectivity (ICA100 edge 835)
3265 - rfMRI connectivity (ICA100 edge 836)
3266 - rfMRI connectivity (ICA100 edge 837)
3267 - rfMRI connectivity (ICA100 edge 838)
3268 - rfMRI connectivity (ICA100 edge 839)
3269 - rfMRI connectivity (ICA100 edge 840)
3270 - rfMRI connectivity (ICA100 edge 841)
3271 - rfMRI connectivity (ICA100 edge 842)
3272 - rfMRI connectivity (ICA100 edge 843)
3273 - rfMRI connectivity (ICA100 edge 844)
3274 - rfMRI connectivity (ICA100 edge 845)
3275 - rfMRI connectivity (ICA100 edge 846)
3276 - rfMRI connectivity (ICA100 edge 847)
3277 - rfMRI connectivity (ICA100 edge 848)
3278 - rfMRI connectivity (ICA100 edge 849)
3279 - rfMRI connectivity (ICA100 edge 850)
3280 - rfMRI connectivity (ICA10

In [52]:
IDP_categories = np.transpose(mat['IDP_categories'], (1,0)).flatten()

IDP_category_names = ['Regional and Tissue Volume',
                      'Cortical Area',
                      'Cortical Thickness',
                      'Regional and Tissue Intensity',
                      'Cortical Grey-White Contrast',
                      'White Matter Hyperintensity Colume',
                      'Regional T2*',
                      'WM Tract FA',
                      'WM Tract MO',
                      'WM Tract Diffusivity',
                      'WM Tract ICVF',
                      'WM Tract OD',
                      'WM Tract ISOVF',
                      'tfMRI Activation',
                      'rfMRI Node Amplitude',
                      'rfMRI Connectivity']

IDP_categories_new = []
for idx, elem in enumerate(IDP_categories):
    IDP_categories_new.append(IDP_category_names[int(elem)-1])
    
if os.path.exists('IDP_categories.txt'):
    os.remove('IDP_categories.txt')
with open('IDP_categories.txt', 'w', newline='') as file:
    for item in IDP_categories_new:
        file.write(item + '\n')

In [53]:
male_train = np.loadtxt('male_train.txt').astype(int)
female_train = np.loadtxt('female_train.txt').astype(int)

male_test = np.loadtxt('male_test.txt').astype(int)
female_test = np.loadtxt('female_test.txt').astype(int)

male_validation = np.loadtxt('male_validation.txt').astype(int)
female_validation = np.loadtxt('female_validation.txt').astype(int)

female_testA = np.loadtxt('female_testA.txt').astype(int)
female_testB = np.loadtxt('female_testB.txt').astype(int)

male_testA = np.loadtxt('male_testA.txt').astype(int)
male_testB = np.loadtxt('male_testB.txt').astype(int)

In [54]:
def check_data(dataset):    
    counter = 0
    for subject in subject_IDs_unique:
        subject = int('2' + str(subject))
        if subject in dataset:
            counter += 1

    print(len(dataset), counter)

    counter = 0
    for subject in dataset:
        subj = subject - 20000000
        if subj not in subject_IDs_unique:
            print('Exlude the following subject:', subject)

In [55]:
check_data(male_train)
check_data(female_train)
check_data(male_test)
check_data(female_test)
check_data(male_validation)
check_data(female_validation)
check_data(female_testA)
check_data(female_testB)

check_data(male_testA)
check_data(male_testB)

8184 8184
9412 9412
4364 4364
5020 5020
1091 1091
1255 1255
2510 2510
2510 2510
2182 2182
2182 2182


In [43]:
# !ls '../../Analysis Male'

In [44]:
subjects_male = []
IDPs1_i_deconfnoage_male = []

for subject in male_train:
    subj = subject - 20000000
    if subj in subject_IDs_unique:
        idx = np.where(subject_IDs_unique == subj)
        subjects_male.append(subject)
        IDPs1_i_deconfnoage_male.append(IDPs1_i_deconfnoage[idx].flatten())
        
subjects_male = np.array(subjects_male)
IDPs1_i_deconfnoage_male = np.array(IDPs1_i_deconfnoage_male)

if os.path.exists('male_train_IDPs.h5'):
    os.remove('male_train_IDPs.h5')
h5f = h5py.File('male_train_IDPs.h5', 'w')
h5f.create_dataset('subjects', data=subjects_male)
h5f.create_dataset('IDPs1_i_deconfnoage_male', data=IDPs1_i_deconfnoage_male)
h5f.close()

test = h5py.File('male_train_IDPs.h5', 'r')
test.keys()
for key in list(test.keys()):
    print(key, test[key].shape)

IDPs1_i_deconfnoage_male (8184, 3921)
subjects (8184,)


In [45]:
subjects_female = []
IDPs1_i_deconfnoage_female = []

for subject in female_train:
    subj = subject - 20000000
    if subj in subject_IDs_unique:
        idx = np.where(subject_IDs_unique == subj)
        subjects_female.append(subject)
        IDPs1_i_deconfnoage_female.append(IDPs1_i_deconfnoage[idx].flatten())
        
subjects_female = np.array(subjects_female)
IDPs1_i_deconfnoage_female = np.array(IDPs1_i_deconfnoage_female)

if os.path.exists('female_train_IDPs.h5'):
    os.remove('female_train_IDPs.h5')
h5f = h5py.File('female_train_IDPs.h5', 'w')
h5f.create_dataset('subjects', data=subjects_female)
h5f.create_dataset('IDPs1_i_deconfnoage_female', data=IDPs1_i_deconfnoage_female)
h5f.close()

test = h5py.File('female_train_IDPs.h5', 'r')
test.keys()
for key in list(test.keys()):
    print(key, test[key].shape)

IDPs1_i_deconfnoage_female (9412, 3921)
subjects (9412,)


In [46]:
h5f.close()

In [48]:
subjects_male = []
IDPs1_i_deconfnoage_male = []

for subject in male_validation:
    subj = subject - 20000000
    if subj in subject_IDs_unique:
        idx = np.where(subject_IDs_unique == subj)
        subjects_male.append(subject)
        IDPs1_i_deconfnoage_male.append(IDPs1_i_deconfnoage[idx].flatten())
        
subjects_male = np.array(subjects_male)
IDPs1_i_deconfnoage_male = np.array(IDPs1_i_deconfnoage_male)

if os.path.exists('male_validation_IDPs.h5'):
    h5f = h5py.File('male_validation_IDPs.h5', 'a')
else:
    h5f = h5py.File('male_validation_IDPs.h5', 'w')
    h5f.create_dataset('subjects', data=subjects_male)

h5f.create_dataset('IDPs1_i_deconfnoage_male', data=IDPs1_i_deconfnoage_male)
h5f.close()

test = h5py.File('male_validation_IDPs.h5', 'r')
test.keys()
for key in list(test.keys()):
    print(key, test[key].shape)
test.close()

OSError: Unable to create file (file exists)

In [49]:
subjects_female = []
IDPs1_i_deconfnoage_female = []

for subject in female_validation:
    subj = subject - 20000000
    if subj in subject_IDs_unique:
        idx = np.where(subject_IDs_unique == subj)
        subjects_female.append(subject)
        IDPs1_i_deconfnoage_female.append(IDPs1_i_deconfnoage[idx].flatten())
        
subjects_female = np.array(subjects_female)
IDPs1_i_deconfnoage_female = np.array(IDPs1_i_deconfnoage_female)

if os.path.exists('female_validation_IDPs.h5'):
    h5f = h5py.File('female_validation_IDPs.h5', 'a')
else:
    h5f = h5py.File('female_validation_IDPs.h5', 'w')
    h5f.create_dataset('subjects', data=subjects_female)

h5f.create_dataset('IDPs1_i_deconfnoage_female', data=IDPs1_i_deconfnoage_female)
h5f.close()

validation = h5py.File('female_validation_IDPs.h5', 'r')
validation.keys()
for key in list(validation.keys()):
    print(key, validation[key].shape)
validation.close()

IDPs1_i_deconf (1255, 3921)
IDPs1_i_deconfnoage_female (1255, 3921)
subjects (1255,)
vars_i_deconf (1255, 17527)


In [50]:
subjects_male = []
IDPs1_i_deconfnoage_male = []

for subject in male_test:
    subj = subject - 20000000
    if subj in subject_IDs_unique:
        idx = np.where(subject_IDs_unique == subj)
        subjects_male.append(subject)
        IDPs1_i_deconfnoage_male.append(IDPs1_i_deconfnoage[idx].flatten())
        
subjects_male = np.array(subjects_male)
IDPs1_i_deconfnoage_male = np.array(IDPs1_i_deconfnoage_male)

if os.path.exists('male_test_IDPs.h5'):
    h5f = h5py.File('male_test_IDPs.h5', 'a')
else:
    h5f = h5py.File('male_test_IDPs.h5', 'w')
    h5f.create_dataset('subjects', data=subjects_male)

h5f.create_dataset('IDPs1_i_deconfnoage_male', data=IDPs1_i_deconfnoage_male)
h5f.close()

test = h5py.File('male_test_IDPs.h5', 'r')
test.keys()
for key in list(test.keys()):
    print(key, test[key].shape)
test.close()

IDPs1_i_deconf (4364, 3921)
IDPs1_i_deconfnoage_male (4364, 3921)
subjects (4364,)
vars_i_deconf (4364, 17527)


In [51]:
subjects_female = []
IDPs1_i_deconfnoage_female = []

for subject in female_test:
    subj = subject - 20000000
    if subj in subject_IDs_unique:
        idx = np.where(subject_IDs_unique == subj)
        subjects_female.append(subject)
        IDPs1_i_deconfnoage_female.append(IDPs1_i_deconfnoage[idx].flatten())
        
subjects_female = np.array(subjects_female)
IDPs1_i_deconfnoage_female = np.array(IDPs1_i_deconfnoage_female)

if os.path.exists('female_test_IDPs.h5'):
    h5f = h5py.File('female_test_IDPs.h5', 'a')
else:
    h5f = h5py.File('female_test_IDPs.h5', 'w')
    h5f.create_dataset('subjects', data=subjects_female)

h5f.create_dataset('IDPs1_i_deconfnoage_female', data=IDPs1_i_deconfnoage_female)
h5f.close()

test = h5py.File('female_test_IDPs.h5', 'r')
test.keys()
for key in list(test.keys()):
    print(key, test[key].shape)
test.close()

IDPs1_i_deconf (5020, 3921)
IDPs1_i_deconfnoage_female (5020, 3921)
subjects (5020,)
vars_i_deconf (5020, 17527)


In [52]:
subjects_female = []
IDPs1_i_deconfnoage_female = []

for subject in female_testA:
    subj = subject - 20000000
    if subj in subject_IDs_unique:
        idx = np.where(subject_IDs_unique == subj)
        subjects_female.append(subject)
        IDPs1_i_deconfnoage_female.append(IDPs1_i_deconfnoage[idx].flatten())
        
subjects_female = np.array(subjects_female)
IDPs1_i_deconfnoage_female = np.array(IDPs1_i_deconfnoage_female)

if os.path.exists('female_testA_IDPs.h5'):
    h5f = h5py.File('female_testA_IDPs.h5', 'a')
else:
    h5f = h5py.File('female_testA_IDPs.h5', 'w')
    h5f.create_dataset('subjects', data=subjects_female)

h5f.create_dataset('IDPs1_i_deconfnoage_female', data=IDPs1_i_deconfnoage_female)
h5f.close()

testA = h5py.File('female_testA_IDPs.h5', 'r')
testA.keys()
for key in list(testA.keys()):
    print(key, testA[key].shape)
testA.close()

IDPs1_i_deconf (2510, 3921)
IDPs1_i_deconfnoage_female (2510, 3921)
subjects (2510,)
vars_i_deconf (2510, 17527)


In [56]:
subjects_female = []
IDPs1_i_deconfnoage_female = []

for subject in female_testB:
    subj = subject - 20000000
    if subj in subject_IDs_unique:
        idx = np.where(subject_IDs_unique == subj)
        subjects_female.append(subject)
        IDPs1_i_deconfnoage_female.append(IDPs1_i_deconfnoage[idx].flatten())
        
subjects_female = np.array(subjects_female)
IDPs1_i_deconfnoage_female = np.array(IDPs1_i_deconfnoage_female)

if os.path.exists('female_testB_IDPs.h5'):
    h5f = h5py.File('female_testB_IDPs.h5', 'a')
else:
    h5f = h5py.File('female_testB_IDPs.h5', 'w')
    h5f.create_dataset('subjects', data=subjects_female)

h5f.create_dataset('IDPs1_i_deconfnoage_female', data=IDPs1_i_deconfnoage_female)
h5f.close()

testB = h5py.File('female_testB_IDPs.h5', 'r')
testB.keys()
for key in list(testB.keys()):
    print(key, testB[key].shape)
testB.close()

IDPs1_i_deconf (2510, 3921)
IDPs1_i_deconfnoage_female (2510, 3921)
subjects (2510,)
vars_i (2510, 17527)
vars_i_deconf (2510, 17527)


In [54]:
subjects_male = []
IDPs1_i_deconfnoage_male = []

for subject in male_testA:
    subj = subject - 20000000
    if subj in subject_IDs_unique:
        idx = np.where(subject_IDs_unique == subj)
        subjects_male.append(subject)
        IDPs1_i_deconfnoage_male.append(IDPs1_i_deconfnoage[idx].flatten())
        
subjects_male = np.array(subjects_male)
IDPs1_i_deconfnoage_male = np.array(IDPs1_i_deconfnoage_male)

if os.path.exists('male_testA_IDPs.h5'):
    h5f = h5py.File('male_testA_IDPs.h5', 'a')
else:
    h5f = h5py.File('male_testA_IDPs.h5', 'w')
    h5f.create_dataset('subjects', data=subjects_male)

h5f.create_dataset('IDPs1_i_deconfnoage_male', data=IDPs1_i_deconfnoage_male)
h5f.close()

testA = h5py.File('male_testA_IDPs.h5', 'r')
testA.keys()
for key in list(testA.keys()):
    print(key, testA[key].shape)
testA.close()

IDPs1_i_deconf (2182, 3921)
IDPs1_i_deconfnoage_male (2182, 3921)
subjects (2182,)
vars_i_deconf (2182, 17527)


In [55]:
subjects_male = []
IDPs1_i_deconfnoage_male = []

for subject in male_testB:
    subj = subject - 20000000
    if subj in subject_IDs_unique:
        idx = np.where(subject_IDs_unique == subj)
        subjects_male.append(subject)
        IDPs1_i_deconfnoage_male.append(IDPs1_i_deconfnoage[idx].flatten())
        
subjects_male = np.array(subjects_male)
IDPs1_i_deconfnoage_male = np.array(IDPs1_i_deconfnoage_male)

if os.path.exists('male_testB_IDPs.h5'):
    h5f = h5py.File('male_testB_IDPs.h5', 'a')
else:
    h5f = h5py.File('male_testB_IDPs.h5', 'w')
    h5f.create_dataset('subjects', data=subjects_male)

h5f.create_dataset('IDPs1_i_deconfnoage_male', data=IDPs1_i_deconfnoage_male)
h5f.close()

testB = h5py.File('male_testB_IDPs.h5', 'r')
testB.keys()
for key in list(testB.keys()):
    print(key, testB[key].shape)
testB.close()

IDPs1_i_deconf (2182, 3921)
IDPs1_i_deconfnoage_male (2182, 3921)
subjects (2182,)
vars_i_deconf (2182, 17527)


In [56]:
!ls '../../Analysis Male New/'

1. MAEs, MSEs, PR + Saving Pandas Dataframes.ipynb
1.2. Train MAEs, MSEs, PR + Saving Pandas Dataframes.ipynb
1.3 Validation MAEs, MSEs, PR + Saving Pandas Dataframes.ipynb
10. ICA-Vars Correlations Analysis - Subject Direction.ipynb
10.1. ICA-Vars Correlations Analysis - Feature Direction.ipynb
10.2. ICA-Vars Correlations Analysis - Reduced Feature Direction.ipynb
11. IDP Predictions.ipynb
11.1. IDP Predictions - with Half B of Test Set.ipynb
11.2. IDP Predictions - MLP.ipynb
2. Correlation, Partial Correlation and Scatter Plots.ipynb
2.1. Correlation, Partial Correlation and Scatter Plots AFTER Deconfounding.ipynb
3. Averages across young and old subjects + Difference Maps + Location Plots  ---- NA FOR MEN.ipynb
4. Naive MAE-based Ensambling.ipynb
5. Multiple Linear Regression Ensembling.ipynb
5.1. ElasticNet & ElasticNet CV.ipynb
5.2. Repeated Elastic Net Technique.ipynb
5.3. PCA Variance & Weights for Ensembles.ipynb
5.4. MLP with CV Grid Search.ipynb
5.5. EBM --- NOT APLICABLE .ip

In [57]:
testA = h5py.File('../../Analysis Male New/male_testA_IDPs.h5', 'r')
testA.keys()
for key in list(testA.keys()):
    print(key, testA[key].shape)
testA.close()

IDPs1_i_deconf (2182, 3921)
IDPs1_i_deconfnoage_male (2182, 3921)
subjects (2182,)
vars_i_deconf (2182, 17527)
